In [2]:
pip install python-dotenv

Note: you may need to restart the kernel to use updated packages.


In [1]:
import requests
import pandas as pd
# Configuración para poder visualizar todas las columnas de los DataFrames
pd.set_option('display.max_columns', None) 
import json
from PIL import Image
from io import BytesIO
import matplotlib.pyplot as plt
import os
from dotenv import load_dotenv


# PASO 1
Para poder conseguir la información requerida en esta fase, usamos la función pd.read_csv, de la biblioteca Pandas: traemos el archivo CSV que obtuvimos de la fase anterior y lo convertirlos en un DataFrame que es almacenado en la variable df_lista_artistas.

In [3]:

df_lista_artistas = pd.read_csv("lista_artistas_spotify.csv")
df_lista_artistas

0
0           Måneskin
1         Elton John
2           Parmalee
3        OneRepublic
4       Thomas Rhett
...              ...
1889   xaviersobased
1890    Quando Rondo
1891      Mighty Bay
1892         50 Cent
1893  Ralfy the Plug

[1894 rows x 1 columns]

# PASO 2
Covertimos el DataFrame en una lista, para poder acceder a la columna que tiene el nombre '0' y así obtener todos los valores de esa columna, o sea, el nombre de los artistas.

In [4]:

artistas = list(df_lista_artistas['0'])
artistas

['Måneskin',
 'Elton John',
 'Parmalee',
 'OneRepublic',
 'Thomas Rhett',
 'Jason Aldean',
 'Elle King',
 'Duran Duran',
 'Imagine Dragons',
 'We Are Messengers',
 'Greta Van Fleet',
 'Sam Hunt',
 'Simple Plan',
 'Twenty One Pilots',
 'Japanese Breakfast',
 'Crowder',
 'Phil Wickham',
 'Jameson Rodgers',
 'Lake Street Dive',
 'Goth Babe',
 'The Neighbourhood',
 'Ryan Hurd',
 'Lauren Daigle',
 'Glass Animals',
 'Mitchell Tenpenny',
 'Disney',
 'Tommy James & The Shondells',
 'Papa Roach',
 'The Hip Abduction',
 'Scotty McCreery',
 'The Wombats',
 'Skylar Grey',
 'Old Dominion',
 'Mac Powell',
 'The Elovaters',
 'Aimer',
 'THE DRIVER ERA',
 'No Vacation',
 'Paul McCartney',
 'Chase Rice',
 'DENM',
 'Saint Motel',
 'Vance Joy',
 'MercyMe',
 'Rob Zombie',
 'The White Stripes',
 'Weezer',
 'Ryan Stevenson',
 'Florida Georgia Line',
 'Bee Gees',
 'Friday Pilots Club',
 'Surfer Girl',
 'Logan Mize',
 'for KING & COUNTRY',
 'Jimmie Allen',
 'if i die in mississippi',
 'Luna Li',
 'Walker Hayes

# PASO 3
Nos registramos en la página de API Last.fm, y así obtuvimos la ClaveApi (Key), la cual es requerida para hacer la llamada. 

Usamos la función load_dotenv(), de la biblioteca python-dotenv, para ocultar nuestra Key al subir el archivo a Git. 

In [5]:
load_dotenv()
api_key = os.getenv("api_key_lastfm")

# PASO 4
Revisamos y analizamos la documentación proporcionada por la Api, y allí obtuvimos la URL para hacer la llamada. Encontramos que La URL raíz de la API se encuentra en "http://ws.audioscrobbler.com/2.0/" y para realizar la busqueda de la información de los artistas por nombre, la completamos con la URL JSON: "/2.0/?method=artist.search&artist=cher&api_key=SU_CLAVE_API&format=json". Encontrar la URL correcta se nos hizo fácil, ya que la documentación no es compleja.

La documentación también nos indicaba los parámetros: limit, page, artist y Api_key, sin embargo, solo artist y Api_key son los obligatorios y fue los que usamos en nuestra URL.

URL ESTRUCTURADA: http://ws.audioscrobbler.com/2.0/?method=artist.getinfo&artist={artista}&api_key={API_KEY}&format=json

# PASO 5
Construimos el donde código que recopilará la información que necesitamos de la Api, sobre artistas. A continuación la explicamos un poco: 

- Inicialización: Creamos un diccionario con listas vacías, para almacenar la información que obtengamos del Bucle For
- Bucle For: Creamos un Bucle For para iterar sobre la lista que obtuvimos en el paso 2, utilizando la URL para hacer la llamada a la API de Last.fm.
- Obtención de datos: Se hace una solicitud GET a la API y se convierte la respuesta a formato JSON.
- Extracción de información:
    - try-except: Se intenta acceder al nombre del artista. Si no se encuentra, se salta a la siguiente iteración.
    - Al lograr acceder a la información, se extraen y añaden a las listas del diccionario la biografía, el número de oyentes, el número de reproducciones y los artistas similares.
    - Para artistas similares fue necesario hacer un Bucle, la info que nos devolvia la API de artistas similares, está estructurada como una lista.
- Resultado: Al final del bucle, la variable "info_artistas", que es el diccionario creado previamente, contiene la información recopilada sobre todos los artistas.

In [6]:
info_artistas = {'Nombre':[],'Biografia':[], 'Listeners':[], 'Playcount':[], 'Artistas similares':[]}

for artista in artistas:
    url = f'http://ws.audioscrobbler.com/2.0/?method=artist.getinfo&artist={artista}&api_key={api_key}&format=json' 

    datos_artista = requests.get(url)
    data = datos_artista.json()
    data
    try:
        info_artistas['Nombre'].append(data['artist']['name'])
    except KeyError:
        continue
    
    info_artistas['Biografia'].append(data['artist']['bio']['content'])
    info_artistas['Listeners'].append(data['artist']['stats']['listeners'])
    info_artistas['Playcount'].append(data['artist']['stats']['playcount'])
    art_similares = []
    for name in data['artist']['similar']['artist']:
        art_similares.append(name['name'])
    info_artistas['Artistas similares'].append(art_similares)

info_artistas


{'Nombre': ['Måneskin',
  'Elton John',
  'Parmalee',
  'OneRepublic',
  'Thomas Rhett',
  'Jason Aldean',
  'Elle King',
  'Duran Duran',
  'Imagine Dragons',
  'We Are Messengers',
  'Greta Van Fleet',
  'Sam Hunt',
  'Simple Plan',
  'Twenty One Pilots',
  'Japanese Breakfast',
  'Crowder',
  'Phil Wickham',
  'Jameson Rodgers',
  'Lake Street Dive',
  'Goth Babe',
  'The Neighbourhood',
  'Ryan Hurd',
  'Lauren Daigle',
  'Glass Animals',
  'Mitchell Tenpenny',
  'Disney',
  'Tommy James ',
  'Papa Roach',
  'The Hip Abduction',
  'Scotty McCreery',
  'The Wombats',
  'Skylar Grey',
  'Old Dominion',
  'Mac Powell',
  'The Elovaters',
  'Aimer',
  'The Driver Era',
  'no vacation',
  'Paul McCartney',
  'Chase Rice',
  'DENM',
  'Saint Motel',
  'Vance Joy',
  'MercyMe',
  'Rob Zombie',
  'The White Stripes',
  'Weezer',
  'Ryan Stevenson',
  'Florida Georgia Line',
  'Bee Gees',
  'Friday Pilots Club',
  'Surfer Girl',
  'Logan Mize',
  'for KING ',
  'Jimmie Allen',
  'if i die i

In [7]:
info_artistas

{'Nombre': ['Måneskin',
  'Elton John',
  'Parmalee',
  'OneRepublic',
  'Thomas Rhett',
  'Jason Aldean',
  'Elle King',
  'Duran Duran',
  'Imagine Dragons',
  'We Are Messengers',
  'Greta Van Fleet',
  'Sam Hunt',
  'Simple Plan',
  'Twenty One Pilots',
  'Japanese Breakfast',
  'Crowder',
  'Phil Wickham',
  'Jameson Rodgers',
  'Lake Street Dive',
  'Goth Babe',
  'The Neighbourhood',
  'Ryan Hurd',
  'Lauren Daigle',
  'Glass Animals',
  'Mitchell Tenpenny',
  'Disney',
  'Tommy James ',
  'Papa Roach',
  'The Hip Abduction',
  'Scotty McCreery',
  'The Wombats',
  'Skylar Grey',
  'Old Dominion',
  'Mac Powell',
  'The Elovaters',
  'Aimer',
  'The Driver Era',
  'no vacation',
  'Paul McCartney',
  'Chase Rice',
  'DENM',
  'Saint Motel',
  'Vance Joy',
  'MercyMe',
  'Rob Zombie',
  'The White Stripes',
  'Weezer',
  'Ryan Stevenson',
  'Florida Georgia Line',
  'Bee Gees',
  'Friday Pilots Club',
  'Surfer Girl',
  'Logan Mize',
  'for KING ',
  'Jimmie Allen',
  'if i die i

# PASO 6
A través de la biblioteca de Pandas, creamos un DataFrame, a partir del diccionario "info_artistas"

In [12]:
df = pd.DataFrame(info_artistas)

df

Nombre                                          Biografia  \
0           Måneskin  Måneskin (Italian pronunciation: ˈmɔːneskin, D...   
1         Elton John  Sir Elton Hercules John (born Reginald Kenneth...   
2           Parmalee  Parmalee is a Country Rock band from North Car...   
3        OneRepublic  OneRepublic is an American pop-rock band forme...   
4       Thomas Rhett  Thomas Rhett Akins, Jr. (born in Valdosta, Geo...   
...              ...                                                ...   
1878   xaviersobased  Xavier Lopez, more prominently known as xavier...   
1879    Quando Rondo  Tyquian Terrel Bowman (born March 23, 1999), b...   
1880      Mighty Bay                                                      
1881         50 Cent  Curtis James Jackson III (born July 6, 1975 in...   
1882  Ralfy The Plug  Ralfy the Plug is an LA-based rapper who is a ...   

     Listeners  Playcount                                 Artistas similares  
0      1394266   73359390  [Palaye Royale, Mahmood, Marco Mengoni, The St...  
1      4356408  122394073  [Billy Joel, Rod Stewart, Paul McCartney, Quee...  
2       107714    1160087  [Jordan Davis, Dustin Lynch, Thomas Rhett, Dyl...  
3      3769502  110645255  [Imagine Dragons, The Script, Maroon 5, Americ...  
4       468442   10985736  [Jordan Davis, Cole Swindell, Dustin Lynch, Ol...  
...        ...        ...                                                ...  
1878    104883   10384597  [phreshboyswag, Tenkay, Lil Shine, OsamaSon, A...  
1879    149008    5012588  [YoungBoy Never Broke Again, NoCap, JayDaYoung...  
1880    111430     641783     [TisaKorean, Lijay, DaBaby, A$AP ANT, Khalil?]  
1881   4053947   81787508  [G-Unit, Lloyd Banks, Obie Trice, Tony Yayo, Y...  
1882     28845     519972  [Drakeo The Ruler, BlueBucksClan, Baby Stone G...  

[1883 rows x 5 columns]

# PASO 7
Guardamos el DataFrame, obtenido en el paso anterior, en un archivo CSV.

In [13]:
df.to_csv('lastfm_df_concatenado.csv')

# PASO 8
Usamos la función .unique() para la limpieza de los artistas repetidos. Creamos un Data Frame de la lista para, posteriormente, exportarlo a .csv y usarlo en la siguiente fase del proyecto. Inicialmente teniamos una lista de aproximadamente 1900 artistas y haciendo la limpieza nos quedó una lista de de 1883 artistas.

In [14]:
lista_artistas = list(df['Nombre'].unique())

df_lista_artistas = pd.DataFrame(lista_artistas)

In [15]:
df_lista_artistas.to_csv('lista_artistas_lastfm.csv', index=False)